In [ ]:
import multiprocessing
print(multiprocessing.cpu_count())

2


### Testing out dedupe

In [ ]:
cd drive/MyDrive

/content/drive/MyDrive


In [ ]:
!git clone https://github.com/DistrictDataLabs/dedupe-examples.git

Cloning into 'dedupe-examples'...
remote: Enumerating objects: 6066, done.
remote: Total 6066 (delta 0), reused 0 (delta 0), pack-reused 6066
Receiving objects: 100% (6066/6066), 5.15 MiB | 5.50 MiB/s, done.
Resolving deltas: 100% (3659/3659), done.


In [ ]:
ls

 citizenship-merged.jpg
'Colab Notebooks'/
 dedupe-examples/
 father-citizenship-merged.jpg
'Fusemachines - CV Siddhartha Shrestha.gdoc'
 HierGAT/
 pan.jpg
 pppp.jpg
 sid_tu_convocation.jpg
'Untitled document.gdoc'
'Worklog- Siddhartha Shrestha.gsheet'


In [ ]:
cd dedupe-examples/csv_example/

/content/drive/MyDrive/dedupe-examples/csv_example


In [ ]:
!pip install unidecode

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 235 kB 5.2 MB/s 


In [ ]:
!pip install future

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
!pip install dedupe==1.10

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 83 kB 1.5 MB/s 
     |████████████████████████████████| 106 kB 78.1 MB/s 
     |████████████████████████████████| 150 kB 50.6 MB/s 
     |████████████████████████████████| 3.6 MB 58.4 MB/s 
     |████████████████████████████████| 583 kB 64.9 MB/s 
     |████████████████████████████████| 194 kB 70.8 MB/s 
     |████████████████████████████████| 55 kB 3.5 MB/s 
     |████████████████████████████████| 71 kB 9.7 MB/s 
     |████████████████████████████████| 254 kB 60.0 MB/s 
     |████████████████████████████████| 254 kB 63.1 MB/s 
     |████████████████████████████████| 972 kB 63.2 MB/s 
     |████████████████████████████████| 239 kB 88.5 MB/s 


In [ ]:
!python csv_example.py

importing data ...
starting active labeling...
Site name : erie neighborhood house erie house
Address : 1347 w erie
Zip : 60622
Phone : None

Site name : erie neighborhood house
Address : 1347 w erie street
Zip : 60642
Phone : 6663430

0/10 positive, 0/10 negative
Do these records refer to the same thing?
(y)es / (n)o / (u)nsure / (f)inished
y
Site name : thresholds mothers? project
Address : 1110 w. belmont
Zip : None
Phone : None

Site name : thresholds mothers' project i/t
Address : 1110 w. belmont
Zip : 60657
Phone : 4720328

1/10 positive, 0/10 negative
Do these records refer to the same thing?
(y)es / (n)o / (u)nsure / (f)inished / (p)revious
y
Site name : onward neighborhood house - tiny town for tots
Address : 5654 w division st
Zip : None
Phone : None

Site name : onward neighborhood house tiny town for tots
Address : 5654 w division st
Zip : 60651
Phone : 6260048

2/10 positive, 0/10 negative
Do these records refer to the same thing?
(y)es / (n)o / (u)nsure / (f)inished / (p)

In [ ]:
!python csv_evaluation.py #can clearly see as we gave 16 positive and 1 negative record for active learning so we get less recall = TP/TP+FN

found duplicate
3289
precision
0.8905442383703254
recall
0.4432506053268765


Dedupe allows to compare on certain feature instead of all field by field. So, that it will help incase there are many fields but only some are important while finding similar records.

### Blocking

Blocking is used to reduce the number of overall record comparison that need to be made.

Dedupe's method of blocking involves engineering subsets of feature vectors. Some rules may be:
- first three digits of the phone number.
- the full name.
- the first five characters of the name.
- a random 4-gram within city name.

Then the record are grouped so that only records with matching rules are compared on active learning.

### Affine gap

It is distance metric which is variation of Hamming distance that makes subsequent consecutive deletions or insertions cheaper.

* ANGIE
* ANGELICA

here we have ANG same so no value for it and we have two characters substution i.e. IE and EL so we assign point 2.

Now we have I new so point 1 for addition.

Finally CA are consecutive addition so .5+.5=1

so, point is 4.


The relative weight of these different feature vectors can be learned during the active learning process and expressed numerically to ensure that features that will be most predictive of matches will be heavier in the overall matching schema.As the user labels more and more tuples, Dedupe gradually relearns the weights, recalculates the edit distances between records, and updates its list of the most uncertain pairs to propose to the user for labeling.

Once the user has generated enough labels, the learned weights are used to calculate the probability that each pair of records within a block is a duplicate or not. In order to scale the pairwise matching up to larger tuples of matched records (in the case that entities may appear more than twice within a document), Dedupe uses hierarchical clustering with centroidal linkage. Records within some threshold distance of a centroid will be grouped together. The final result is an annotated version of the original dataset that now includes a centroid label for each record.



### Active Learning

Ask prompts to the user if the records are same or not with four options:
* YES
* NO
* UNSURE
* FINISHED



In [ ]:
import pandas as pd

data = pd.read_csv("/content/drive/MyDrive/data_for_ER/WhiteHouse-WAVES-Released-1210.csv")

/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:3326: DtypeWarning: Columns (4,13) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


In [ ]:
data.head()

NAMELAST NAMEFIRST NAMEMID     UIN BDGNBR ACCESS_TYPE  TOA  POA  TOD  \
0       ROGERS     JAMES       B  U34833    NaN          VA  NaN  NaN  NaN   
1       ROGERS    PAMELA       L  U34833    NaN          VA  NaN  NaN  NaN   
2  WALDSCHMIDT      RYAN       F  U34669    NaN          VA  NaN  NaN  NaN   
3  WALDSCHMIDT      SARA       A  U34669    NaN          VA  NaN  NaN  NaN   
4        DAVIS      LISA       M  U34669    NaN          VA  NaN  NaN  NaN   

   POD  ... TERMINAL_SUFFIX visitee_namelast visitee_namefirst MEETING_LOC  \
0  NaN  ...              J7           OFFICE          VISITORS          WH   
1  NaN  ...              J7           OFFICE          VISITORS          WH   
2  NaN  ...              P6           OFFICE          VISITORS          WH   
3  NaN  ...              P6           OFFICE          VISITORS          WH   
4  NaN  ...              P6           OFFICE          VISITORS          WH   

   MEETING_ROOM CALLER_NAME_LAST CALLER_NAME_FIRST CALLER_ROOM  \
0     RESIDENCE           OFFICE          VISITORS   RESIDENCE   
1     RESIDENCE           OFFICE          VISITORS   RESIDENCE   
2     RESIDENCE           OFFICE          VISITORS   RESIDENCE   
3     RESIDENCE           OFFICE          VISITORS   RESIDENCE   
4     RESIDENCE           OFFICE          VISITORS   RESIDENCE   

       Description RELEASE_DATE  
0  MERGE TO U35166    1/29/2010  
1  MERGE TO U35166    1/29/2010  
2  MERGE TO U34505    1/29/2010  
3  MERGE TO U34505    1/29/2010  
4  MERGE TO U34505   12/30/2009  

[5 rows x 28 columns]

In [ ]:
len(data)

968907

In [ ]:
new_data = data.drop(data[data.NAMELAST.str.contains(r'[^0-9a-zA-Z]') |
         data.NAMEFIRST.str.contains(r'[^0-9a-zA-Z]')].index).reset_index()

In [ ]:
new_data.tail()

index   NAMELAST NAMEFIRST NAMEMID     UIN   BDGNBR ACCESS_TYPE  \
968564  968902  ZUMWINKLE      MIKE     NaN  U38215  79841.0          VA   
968565  968903   ZURAWSKI      PAUL       R  U41111  76629.0          VA   
968566  968904     ZUTTAH   JEFFREY     NaN  U41130  75913.0          VA   
968567  968905     ZUTTAH   JEFFREY     NaN  U43381  76627.0          VA   
968568  968906  ZWERDLING    HILARY       C  U38761      NaN          VA   

                    TOA    POA              TOD  ... TERMINAL_SUFFIX  \
968564   9/3/2010 16:47  B0402              NaN  ...              LC   
968565  9/15/2010 14:42  A0401  9/15/2010 15:59  ...              T1   
968566   9/16/2010 9:51  D1S01  9/16/2010 10:44  ...              DC   
968567  9/22/2010 10:05   K101              NaN  ...              T1   
968568              NaN    NaN              NaN  ...              B9   

       visitee_namelast visitee_namefirst MEETING_LOC MEETING_ROOM  \
968564        ALHASSANI             MEHDI          WH           WW   
968565           FURMAN             JASON          WH           WW   
968566          GOODMAN              MARY        OEOB          495   
968567           ABRAMS            ANDREW        NEOB         2211   
968568            PAPAS              NICK          WH   SOUTH LAWN   

        CALLER_NAME_LAST CALLER_NAME_FIRST CALLER_ROOM Description  \
968564         ALHASSANI             MEHDI         NaN         NaN   
968565            SIEGEL              AVRA         NaN         NaN   
968566           WATKINS              KYLE         NaN         NaN   
968567           FERRELL          PATRICIA         NaN         NaN   
968568            WHITTY           PATRICK         NaN         NaN   

       RELEASE_DATE  
968564   12/31/2010  
968565   12/31/2010  
968566   12/31/2010  
968567   12/31/2010  
968568   12/31/2010  

[5 rows x 29 columns]

In [ ]:
new_data.columns

Index(['index', 'NAMELAST', 'NAMEFIRST', 'NAMEMID', 'UIN', 'BDGNBR',
       'ACCESS_TYPE', 'TOA', 'POA', 'TOD', 'POD', 'APPT_MADE_DATE',
       'APPT_START_DATE', 'APPT_END_DATE', 'APPT_CANCEL_DATE', 'Total_People',
       'LAST_UPDATEDBY', 'POST', 'LastEntryDate', 'TERMINAL_SUFFIX',
       'visitee_namelast', 'visitee_namefirst', 'MEETING_LOC', 'MEETING_ROOM',
       'CALLER_NAME_LAST', 'CALLER_NAME_FIRST', 'CALLER_ROOM', 'Description',
       'RELEASE_DATE'],
      dtype='object')

In [ ]:
new_data.to_csv("/content/drive/MyDrive/data_for_ER/new_data.csv",index=False)

In [ ]:
import tempfile
import argparse
import csv
import os
import dedupe

In [ ]:
FIELDS =  [{'field': 'NAMEFIRST',
               'type': 'String','has missing': True},
              {'field': 'NAMELAST',
               'type': 'String','has missing': True},
              {'field': 'UIN',
               'type': 'String','has missing': True},
              {'field': 'MEETING_LOC',
               'type': 'String','has missing': True}
              ]

In [ ]:
# Create a new deduper object and pass our data model to it.
deduper = dedupe.Dedupe(FIELDS)

In [ ]:
from unidecode import unidecode
import re

def preProcess(column):
  """
  Do a little bit of data cleaning with the help of Unidecode and Regex.
  Things like casing, extra spaces, quotes and new lines can be ignored.
  """
  column = unidecode(column)
  column = re.sub('  +', ' ', column)
  column = re.sub('\n', ' ', column)
  column = column.strip().strip('"').strip("'").lower().strip()
  # If data is missing, indicate that by setting the value to `None`
  if not column:
    column = None
  return column

def readData(filename):
  """
  Read in our data from a CSV file and create a dictionary of records,
  where the key is a unique record ID and each value is dict
  """

  data_d = {}
  with open(filename) as f:
    reader = csv.DictReader(f)
    for row in reader:
      clean_row = [(k, preProcess(v)) for (k, v) in row.items()]
      row_id = int(row['index'])
      data_d[row_id] = dict(clean_row)

  return data_d

In [ ]:
data_d = readData("/content/drive/MyDrive/data_for_ER/new_data.csv")

In [ ]:
data_d

{0: {'index': '0',
  'NAMELAST': 'rogers',
  'NAMEFIRST': 'james',
  'NAMEMID': 'b',
  'UIN': 'u34833',
  'BDGNBR': None,
  'ACCESS_TYPE': 'va',
  'TOA': None,
  'POA': None,
  'TOD': None,
  'POD': None,
  'APPT_MADE_DATE': '9/5/2009 10:52',
  'APPT_START_DATE': '9/8/2009 10:30',
  'APPT_END_DATE': '9/8/2009 23:59',
  'APPT_CANCEL_DATE': '9/7/2009 14:34',
  'Total_People': '110.0',
  'LAST_UPDATEDBY': 'j7',
  'POST': 'win',
  'LastEntryDate': '9/5/2009 11:00',
  'TERMINAL_SUFFIX': 'j7',
  'visitee_namelast': 'office',
  'visitee_namefirst': 'visitors',
  'MEETING_LOC': 'wh',
  'MEETING_ROOM': 'residence',
  'CALLER_NAME_LAST': 'office',
  'CALLER_NAME_FIRST': 'visitors',
  'CALLER_ROOM': 'residence',
  'Description': 'merge to u35166',
  'RELEASE_DATE': '1/29/2010'},
 1: {'index': '1',
  'NAMELAST': 'rogers',
  'NAMEFIRST': 'pamela',
  'NAMEMID': 'l',
  'UIN': 'u34833',
  'BDGNBR': None,
  'ACCESS_TYPE': 'va',
  'TOA': None,
  'POA': None,
  'TOD': None,
  'POD': None,
  'APPT_MADE_DA

In [ ]:
import json
with open("/content/drive/MyDrive/data_for_ER/data.json", "w") as write_file:
  json.dump(data_d, write_file, indent=4)

In [ ]:
deduper.prepare_training(data_d)
#Initialize the active learner with your data

In [ ]:
dedupe.consoleLabel(deduper)

NAMEFIRST : michele
NAMELAST : brown
UIN : u31894
MEETING_LOC : wh

NAMEFIRST : miichelle
NAMELAST : brown
UIN : u31894
MEETING_LOC : wh

0/10 positive, 0/10 negative
Do these records refer to the same thing?
(y)es / (n)o / (u)nsure / (f)inished


y


NAMEFIRST : benjamin
NAMELAST : smith
UIN : u94730
MEETING_LOC : wh

NAMEFIRST : jenna
NAMELAST : smith
UIN : u94730
MEETING_LOC : wh

1/10 positive, 0/10 negative
Do these records refer to the same thing?
(y)es / (n)o / (u)nsure / (f)inished / (p)revious


n


NAMEFIRST : natalie
NAMELAST : lew
UIN : u03994
MEETING_LOC : wh

NAMEFIRST : natalie
NAMELAST : hawkins
UIN : None
MEETING_LOC : vpr

1/10 positive, 1/10 negative
Do these records refer to the same thing?
(y)es / (n)o / (u)nsure / (f)inished / (p)revious


...

NAMEFIRST : james
NAMELAST : rice
UIN : u02071
MEETING_LOC : neob

NAMEFIRST : james
NAMELAST : rice
UIN : u44297
MEETING_LOC : neob

11/10 positive, 11/10 negative
Do these records refer to the same thing?
(y)es / (n)o / (u)nsure / (f)inished / (p)revious


y


NAMEFIRST : lee
NAMELAST : sachs
UIN : u52030
MEETING_LOC : oeob

NAMEFIRST : lee
NAMELAST : sachs
UIN : u04384
MEETING_LOC : oeob

12/10 positive, 11/10 negative
Do these records refer to the same thing?
(y)es / (n)o / (u)nsure / (f)inished / (p)revious


f


Finished labeling


In [ ]:
deduper.train()

In [ ]:
with open("/content/drive/MyDrive/data_for_ER/training.json", 'w') as tf:
  deduper.writeTraining(tf)

In [ ]:
with open("/content/drive/MyDrive/data_for_ER/settings", 'wb') as sf:
  deduper.writeSettings(sf)

In [ ]:
# clustered_dupes = deduper.partition(data_d, 0.5)

clustered_dupes = deduper.match(data_d, 0.5)
#0.5 is threshold We will only consider put together records into clusters if the cophenetic similarity of the cluster is greater than the threshold.
# Lowering the number will increase recall, raising it will increase precision

For match the docs suggest to only use on small to moderately sized datasets.

So, we can use matchBlocks. So,we first need to create our own blocks and then pass it to matchBlocks. Doing some research what i found was here is no difference between calling _blockData and then matchBlocks versus just match. Indeed if you look at the code, you'll see that match calls those two methods.

The reason why matchBlocks is exposed is that _blockData can take a lot of memory, and you may want to generate the blocks another way

In [ ]:
cluster_membership = {}
for cluster_id, (records, scores) in enumerate(clustered_dupes):
  for record_id, score in zip(records, scores):
    cluster_membership[record_id] = {
        "Cluster ID": cluster_id,
        "confidence_score": score
    }

In [ ]:
cluster_membership

{0: {'Cluster ID': 0, 'confidence_score': 0.9784596919003131},
 69313: {'Cluster ID': 0, 'confidence_score': 0.9809737829530898},
 94425: {'Cluster ID': 0, 'confidence_score': 0.9797192770296765},
 107108: {'Cluster ID': 0, 'confidence_score': 0.9797634654790074},
 291853: {'Cluster ID': 0, 'confidence_score': 0.9796724963982364},
 358618: {'Cluster ID': 0, 'confidence_score': 0.982549960702445},
 358619: {'Cluster ID': 0, 'confidence_score': 0.977191767060662},
 505796: {'Cluster ID': 0, 'confidence_score': 0.9796723593853374},
 505797: {'Cluster ID': 0, 'confidence_score': 0.9784168209285012},
 505798: {'Cluster ID': 0, 'confidence_score': 0.9761517317713685},
 505799: {'Cluster ID': 0, 'confidence_score': 0.9798508229696129},
 505800: {'Cluster ID': 0, 'confidence_score': 0.9795932080639284},
 505801: {'Cluster ID': 0, 'confidence_score': 0.9999923808835495},
 575489: {'Cluster ID': 0, 'confidence_score': 0.9709954027992014},
 575490: {'Cluster ID': 0, 'confidence_score': 0.97953835

In [ ]:
id = []
for i,v in cluster_membership.items():
  if(v["Cluster ID"]==207):
    id.append(i)

In [ ]:
id

[207,
 20501,
 270718,
 270719,
 479533,
 479534,
 479535,
 479536,
 479537,
 479538,
 479539,
 628700,
 681517,
 681518,
 699797,
 775467,
 872501,
 872502]

In [ ]:
lst_data = []
for i in id:
  lst_data.append(data_d[i])

In [ ]:
import pandas as pd
pd.DataFrame(lst_data)

index NAMELAST NAMEFIRST NAMEMID     UIN   BDGNBR ACCESS_TYPE  \
0      207    lopez     maria    None  u40442     None          va   
1    20501    lopez     maria       k  u15518     None          va   
2   270718    lopez     maria    None  u90252     None          va   
3   270719    lopez     maria       i  u89280     None          va   
4   479533    lopez     maria    None  u67754     None          va   
5   479534    lopez     maria       a  u67078     None          va   
6   479535    lopez     maria    None  u66253     None          va   
7   479536    lopez     maria    None  open10     None          al   
8   479537    lopez     maria    None  u63985     None          va   
9   479538    lopez     maria       a  u64796     None          va   
10  479539    lopez     maria    None  u61402      0.0          va   
11  628700    lopez     maria       s  u43377     None          va   
12  681517    lopez     maria    None  u41246     None          va   
13  681518    lopez     maria    None  u40409     None          va   
14  699797    lopez     maria    None  u14347      0.0          va   
15  775467    lopez     maria    None  u19302     None          va   
16  872501    lopez     maria       e  u31599  79844.0          va   
17  872502    lopez     maria       c  u32591     None          va   

                TOA    POA              TOD  ... TERMINAL_SUFFIX  \
0              None   None             None  ...              ks   
1              None   None             None  ...              rc   
2              None   None             None  ...              yt   
3              None   None             None  ...              l6   
4              None   None             None  ...              p6   
5              None   None             None  ...              lc   
6              None   None             None  ...              b3   
7              None   None             None  ...              b9   
8              None   None             None  ...              dc   
9              None   None             None  ...              rc   
10   12/4/2009 9:49  vis01             None  ...              b9   
11             None   None             None  ...              gb   
12             None   None             None  ...              b9   
13             None   None             None  ...              j7   
14   6/8/2010 19:24  vis01             None  ...              j7   
15             None   None             None  ...              sl   
16  8/12/2010 12:49  d1s01  8/12/2010 14:33  ...              sl   
17             None   None             None  ...              lc   

   visitee_namelast visitee_namefirst MEETING_LOC MEETING_ROOM  \
0            office          visitors          wh    residence   
1            office          visitors          wh    residence   
2            office          visitors          wh    residence   
3            office          visitors          wh    residence   
4           martins            carmen          wh    residence   
5            office          visitors          wh    residence   
6            office          visitors          wh    residence   
7            office          visitors          wh    residence   
8            office          visitors          wh    residence   
9            office          visitors          wh    residence   
10           office          visitors          wh    residence   
11           office          visitors          wh    residence   
12           office          visitors          wh    residence   
13           office          visitors          wh    residence   
14            potus              None          wh   south lawn   
15           office          visitors          wh          res   
16             pope             david        oeob          230   
17           office          visitors          wh    residence   

   CALLER_NAME_LAST CALLER_NAME_FIRST CALLER_ROOM           Description  \
0            office          visitors        None  

In [ ]:
with open("/content/drive/MyDrive/data_for_ER/output.csv", 'w') as f_output, open("/content/drive/MyDrive/data_for_ER/new_data.csv") as f_input:

  reader = csv.DictReader(f_input)
  fieldnames = ['Cluster ID', 'confidence_score'] + reader.fieldnames

  writer = csv.DictWriter(f_output, fieldnames=fieldnames)
  writer.writeheader()
  for row in reader:
    print(row)
    row_id = int(row['index'])
    if (row_id not in list(cluster_membership.keys())):
      continue
    row.update(cluster_membership[row_id])
    writer.writerow(row)

10000


KeyboardInterrupt: ignored

In [ ]:
blocks = deduper._blockData(data_d)

In [ ]:
blocks

<generator object DedupeMatching._blockData at 0x7f5cb98baed0>

In [ ]:
clustered_dupes_1 = deduper.matchBlocks(blocks)

In [ ]:
cluster_membership_1 = {}
for cluster_id, (records, scores) in enumerate(clustered_dupes_1):
  for record_id, score in zip(records, scores):
    cluster_membership_1[record_id] = {
        "Cluster ID": cluster_id,
        "confidence_score": score
    }

In [ ]:
cluster_membership_1

{0: {'Cluster ID': 0, 'confidence_score': 0.9784596919003131},
 69313: {'Cluster ID': 0, 'confidence_score': 0.9809737829530898},
 94425: {'Cluster ID': 0, 'confidence_score': 0.9797192770296765},
 107108: {'Cluster ID': 0, 'confidence_score': 0.9797634654790074},
 291853: {'Cluster ID': 0, 'confidence_score': 0.9796724963982364},
 358618: {'Cluster ID': 0, 'confidence_score': 0.982549960702445},
 358619: {'Cluster ID': 0, 'confidence_score': 0.977191767060662},
 505796: {'Cluster ID': 0, 'confidence_score': 0.9796723593853374},
 505797: {'Cluster ID': 0, 'confidence_score': 0.9784168209285012},
 505798: {'Cluster ID': 0, 'confidence_score': 0.9761517317713685},
 505799: {'Cluster ID': 0, 'confidence_score': 0.9798508229696129},
 505800: {'Cluster ID': 0, 'confidence_score': 0.9795932080639284},
 505801: {'Cluster ID': 0, 'confidence_score': 0.9999923808835495},
 575489: {'Cluster ID': 0, 'confidence_score': 0.9709954027992014},
 575490: {'Cluster ID': 0, 'confidence_score': 0.97953835

### Once trained

In [ ]:
with open("/content/drive/MyDrive/data_for_ER/settings", 'rb') as f:
  deduper = dedupe.StaticDedupe(f)

In [ ]:
deduper.threshold(data_d,recall_weight=2)
#recall_weight -- Sets the tradeoff between precision and recall. I.e. if you care twice as much about recall as you do precision, set recall_weight to 2.

0.1881396

In [ ]:
deduper.threshold(data_d,recall_weight=1)

0.43874553

In [ ]:
deduper.threshold(data_d, recall_weight=0.7)

0.6878289

In [ ]:
blocks = deduper._blockData(data_d)

In [ ]:
clustered_dupes_1 = deduper.matchBlocks(blocks)

In [ ]:
cluster_membership_1 = {}
for cluster_id, (records, scores) in enumerate(clustered_dupes_1):
  for record_id, score in zip(records, scores):
    cluster_membership_1[record_id] = {
        "Cluster ID": cluster_id,
        "confidence_score": score
    }

In [ ]:
cluster_membership_1

{0: {'Cluster ID': 0, 'confidence_score': 0.9784596919003131},
 69313: {'Cluster ID': 0, 'confidence_score': 0.9809737829530898},
 94425: {'Cluster ID': 0, 'confidence_score': 0.9797192770296765},
 107108: {'Cluster ID': 0, 'confidence_score': 0.9797634654790074},
 291853: {'Cluster ID': 0, 'confidence_score': 0.9796724963982364},
 358618: {'Cluster ID': 0, 'confidence_score': 0.982549960702445},
 358619: {'Cluster ID': 0, 'confidence_score': 0.977191767060662},
 505796: {'Cluster ID': 0, 'confidence_score': 0.9796723593853374},
 505797: {'Cluster ID': 0, 'confidence_score': 0.9784168209285012},
 505798: {'Cluster ID': 0, 'confidence_score': 0.9761517317713685},
 505799: {'Cluster ID': 0, 'confidence_score': 0.9798508229696129},
 505800: {'Cluster ID': 0, 'confidence_score': 0.9795932080639284},
 505801: {'Cluster ID': 0, 'confidence_score': 0.9999923808835495},
 575489: {'Cluster ID': 0, 'confidence_score': 0.9709954027992014},
 575490: {'Cluster ID': 0, 'confidence_score': 0.97953835

In [ ]:
print(cluster_id)

142405


In [ ]:
deduper.data_model.primary_fields

[(NAMEFIRST: String), (NAMELAST: String), (UIN: String), (MEETING_LOC: String)]

In [ ]:
fields = {variable.field for variable in deduper.data_model.primary_fields}

In [ ]:
fields

{'MEETING_LOC', 'NAMEFIRST', 'NAMELAST', 'UIN'}

In [ ]:
record_hash = hash(tuple(record[f] for f in fields))

In [ ]:
for key, record in data_d.items():
  print(key, record)

Streaming output truncated to the last 5000 lines.
3030 {'index': '3030', 'NAMELAST': 'samuels', 'NAMEFIRST': 'ian', 'NAMEMID': 'h', 'UIN': 'u14105', 'BDGNBR': None, 'ACCESS_TYPE': 'va', 'TOA': None, 'POA': None, 'TOD': None, 'POD': None, 'APPT_MADE_DATE': '6/22/2010 16:10', 'APPT_START_DATE': '6/29/2010 15:00', 'APPT_END_DATE': '6/29/2010 23:59', 'APPT_CANCEL_DATE': '6/29/2010 15:31', 'Total_People': '0.0', 'LAST_UPDATEDBY': 'gb', 'POST': 'win', 'LastEntryDate': '6/22/2010 16:10', 'TERMINAL_SUFFIX': 'gb', 'visitee_namelast': 'office', 'visitee_namefirst': 'visitors', 'MEETING_LOC': 'wh', 'MEETING_ROOM': 's. grounds', 'CALLER_NAME_LAST': 'office', 'CALLER_NAME_FIRST': 'visitors', 'CALLER_ROOM': 's. grounds', 'Description': 'appointee event /', 'RELEASE_DATE': None}
3031 {'index': '3031', 'NAMELAST': 'sanchez', 'NAMEFIRST': 'diego', 'NAMEMID': 'm', 'UIN': 'u14105', 'BDGNBR': None, 'ACCESS_TYPE': 'va', 'TOA': None, 'POA': None, 'TOD': None, 'POD': None, 'APPT_MADE_DATE': '6/9/2010 18:24'

KeyboardInterrupt: ignored

In [ ]:
def exact_matches(data_d, match_fields):
  unique = {}
  redundant = {}
  for key, record in data_d.items():
    record_hash = hash(tuple(record[f] for f in match_fields))
    if record_hash not in redundant:
      unique[key] = record
      redundant[record_hash] = (key, [])
    else:
      redundant[record_hash][1].append(key)

  return unique, {k : v for k, v in redundant.values()}

In [ ]:
unique_d, parents = exact_matches(data_d, fields)

In [ ]:
unique_d

In [ ]:
hash("hello how do you do")

-3175540564081414791